In [ ]:
# scrape more:
# directors
# In release http://www.boxofficemojo.com/movies/?page=main&id=justiceismind.htm
# Runtime

In [15]:
# scraping

from bs4 import BeautifulSoup
import requests
import time
import re
import string

# data manipulation

import dateutil.parser
import pickle
from datetime import datetime
import pprint as pp

# analysis
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

In [19]:
# add print statements
# add logging
# clean up variation naming and comments

In [16]:
# helper function - 

def make_soup(any_url):
    response = requests.get(any_url)
    page = response.text
    soup = BeautifulSoup(page,'lxml')
    return soup

In [17]:
# helper function - 

def get_movie_value(soup, field_name):
    obj = soup.find(text=re.compile(field_name))
    if not obj:
        return None
    
    next_sibling = obj.findNextSibling()
    # identifies the sibling, which is the next attribute
    if next_sibling:
        return next_sibling.text
    else:
        return None

In [18]:
# helper function

def to_date(datestring):
    date = dateutil.parser.parse(datestring)
    return date

In [99]:
def money_to_int(moneystring):
    moneystring = moneystring.replace('$', '').replace(',', '')
    try:
        return int(moneystring)
    except:
        return None

In [24]:
def get_movie_links():
    """
    get movies urls for all movies on Box Office Mojo in a list
    """

    movie_links = [] # create empty list

    alphabet = ["NUM"] + list(string.ascii_uppercase)

    for letter in alphabet:
        for num in range(1,15):
            link_url = (starting_url + 'letter=' + letter + '&page=' + str(num) + '&p=.htm')
            try:
                page = requests.get(link_url).text
                soup = BeautifulSoup(page, 'lxml')
                rows = soup.find("td", text="Title (click to view box office)").find_parent("table").find_all("tr")
                if len(rows) > 1:
                    if link_url not in movie_links:
                        movie_links.append(link_url)
            except:
                continue

    return movie_links

In [25]:
base_url = 'http://www.boxofficemojo.com'
starting_url = 'http://www.boxofficemojo.com/movies/alphabetical.htm?'

movie_index_links = get_movie_links()

In [ ]:
len(movie_index_links)

158

In [ ]:
pagelist = movie_index_links

movie_list = []

# add a print statement

for page in pagelist:
    url = page
    response = requests.get(url)
    soup = BeautifulSoup(response.text,'lxml')
    for x in soup.find_all('a'):
        try:
            if "/movies/?id" in x['href']:
                movie_list.append(x['href'])
                time.sleep(0.1)
            else:
                continue
        except:
            continue
            
htmllist = []
for x in movie_list:
    htmllist.append('http://www.boxofficemojo.com'+x+'&adjust_yr=2015&p=.htm')
    
htmllist = list(set(htmllist))

with open('htmllist.pkl', 'wb') as picklefile:
            pickle.dump(htmllist, picklefile)

### Pick up point - list of individual movie URLs

In [20]:
with open('htmllist.pkl', 'rb') as picklefile: 
    list_of_urls = pickle.load(picklefile)
    
print('Number of links: ', len(movie_ids))

Number of links:  0


In [6]:
len(list_of_urls)

16680

In [44]:
def find_movie_data(urlname):
    try:
        page = requests.get(urlname).text
    except:
        return None
    else:
        soup_name = BeautifulSoup(page,'lxml')
    
        # get movie title
        for title in soup_name:
            try:
                title_string = soup_name.find('title').text
                title = title_string.split('(')[0].strip()
                print('SCRAPING ' + title)
            except:
                print('WARNING: unable to get movie title')
                return None
        
        # get release date
        for release_date in soup_name:
            try:
                raw_release = get_movie_value(soup_name, 'Release Date')
            except:
                print('WARNING: release date not found!')
                return None
            try:
                release = to_date(raw_release)
            except:
                print('WARNING: converted date not working!')
                return None
            if release.year <=1998: 
                return None
                
        # get distributor name
        for distributor in soup_name:
            try:
                dist_comp = get_movie_value(soup_name, 'Distributor')
            except:
                print('WARNING: no distributor data returned')
                return None

        # get MPAA movie rating
        for movie_rating in soup_name:
            try:
                rating = get_movie_value(soup_name, 'MPAA Rating')
            except:
                print('WARNING: no MPAA rating data returned')
                return None

        # get movie genre
        for movie_genre in soup_name:
            try:
                genre = get_movie_value(soup_name, 'Genre:')
            except:
                print('WARNING: no movie genre data returned')
                return None
        
        # get production budget
        for production_budget in soup_name:
            try:
                raw_prod_bud = get_movie_value(soup_name, 'Production Budget')
            except:
                print('WARNING: no production budget data returned')
                None
            if raw_prod_bud == ('N/A'):
                prod_bud = np.nan
            else:
                prod_bud = raw_prod_bud.replace('$', '').replace(' million', '')
        
        # get domestic total gross - table 2
        a_domestic_total = 0
        try:
            a_domestic_total_str = soup_name.find(text="Domestic:").find_parent("td").find_next_sibling("td").get_text(strip=True)
            a_domestic_total_ = a_domestic_total_str.replace('$','').replace(',','')
            a_domestic_total = int(a_domestic_total_)
        except:
            print('WARNING: no domestic total_a gross data returned')
            a_domestic_total = 0
        
        # get foreign total gross
        foreign_total = 0
        try:
            foreign_total_str = soup_name.find(text="Foreign:").find_parent("td").find_next_sibling("td").get_text(strip=True)
            foreign_total = foreign_total_str.replace('$','').replace(',','')
            foreign_total = int(foreign_total)
        except:
            print('WARNING: no foreign total gross data returned')
            foreign_total = 0
        
        # get opening weekend domestic gross total
        open_wkd_gross = 0
        try:
            if len(soup_name.find_all(class_='mp_box_content')[1].find_all('tr')) > 7:
                try:
                    wide_open_wkd_gross_str = soup_name.find_all(class_='mp_box_content')[1].find_all('tr')[3].get_text(strip=True)
                    wide_open_wkd_gross_ = wide_open_wkd_gross_str.split(':',)[1]
                    wide_open_wkd_gross = int(wide_open_wkd_gross_.replace('$','').replace(',',''))
                    
                    limited_open_wkd_gross_str = soup_name.find_all(class_='mp_box_content')[1].find_all('tr')[1].get_text(strip=True)
                    limited_open_wkd_gross_ = limited_open_wkd_gross_str.split(':',)[1]
                    limited_open_wkd_gross = int(limited_open_wkd_gross_.replace('$','').replace(',',''))
                    
                    open_wkd_gross = wide_open_wkd_gross + limited_open_wkd_gross
                except:
                    print('WARNING: no opening weekend domestic gross total data returned')
                    open_wkd_gross = 0
            else:
                try:
                    open_wkd_gross_str = soup_name.find_all(class_='mp_box_content')[1].find_all('tr')[0].get_text(strip=True)
                    open_wkd_gross_ = open_wkd_gross_str.split(':')[1]
                    open_wkd_gross = int(open_wkd_gross_.replace('$','').replace(',',''))                    
                except:
                    print('WARNING: no opening weekend domestic gross total data returned')
                    open_wkd_gross = 0
        except:
            open_wkd_gross = 0
                
        # get opening weekend ranking
        opening_ranking = 0
        try:
            if len(soup_name.find_all(class_='mp_box_content')[1].find_all('tr')) > 7:
                try:
                    opening_ranking_str = soup_name.find_all(class_='mp_box_content')[1].find_all('tr')[4].get_text(strip=True)
                    opening_ranking_ = opening_ranking_str.replace(',','')
                    opening_ranking = int(re.findall('\d+', opening_ranking_)[0])
                except:
                    print('WARNING: no opening weekend domestic gross total data returned')
                    opening_ranking = 0
            else:
                try:
                    opening_ranking_str = soup_name.find_all(class_='mp_box_content')[1].find_all('tr')[1].get_text(strip=True)
                    opening_ranking_ = opening_ranking_str.replace(',','')
                    opening_ranking = int(re.findall('\d+', opening_ranking_)[0])
                except:
                    print('WARNING: no opening weekend domestic gross total data returned')
                    opening_ranking = 0
        except:
            opening_ranking = 0
            
        # get widest release
        widest_release = 0
        try:
            if len(soup_name.find_all(class_='mp_box_content')[1].find_all('tr')) > 7:
                try:
                    widest_release_str = soup_name.find_all(class_='mp_box_content')[1].find_all('table')[3].find('tr').get_text(strip=True)
                    widest_release_ = widest_release_str.replace(',','')
                    widest_release = int(re.findall('\d+', widest_release_)[0])
                except:
                    print('WARNING: no wide release data returned')
                    widest_release = 0
            else:
                try:
                    widest_release_str = soup_name.find_all(class_='mp_box_content')[1].find_all('table')[1].find('tr').get_text(strip=True)
                    widest_release_ = widest_release_str.replace(',','')
                    widest_release = int(re.findall('\d+', widest_release_)[0])
                except:
                    print('WARNING: no wide release data returned')
                    widest_release = 0
        except:
            widest_release = 0

        # get close day
        close_date = 0
        try:
            if len(soup_name.find_all(class_='mp_box_content')[1].find_all('tr')) > 7:
                try:
                    close_date_str = soup_name.find_all(class_='mp_box_content')[1].find_all('table')[4].find('tr').get_text(strip=True)
                    close_date_ = close_date_str.split(':',)[1]
                    close_date = to_date(close_date_)
                except:
                    print('WARNING: no end date returned')
                    close_date = 0
            else:
                try:
                    close_date_str = soup_name.find_all(class_='mp_box_content')[1].find_all('table')[2].find('tr').get_text(strip=True)
                    close_date_ = close_date_str.split(':',)[1]
                    close_date = to_date(close_date_)
                except:
                    print('WARNING: no end date returned')
                    close_date = 0
        except:
            close_date = 0
            
    # return a tuple for each movie with relevant data
    return (title, dist_comp, rating, genre, prod_bud, release, a_domestic_total, 
            foreign_total, open_wkd_gross, opening_ranking, widest_release, close_date)

In [45]:
list_of_urls_1 = list_of_urls[:4000]
list_of_urls_2 = list_of_urls[3999:8000]
list_of_urls_3 = list_of_urls[7999:12000]
list_of_urls_4 = list_of_urls[11999:16000]
list_of_urls_5 = list_of_urls[15999:16681]

In [46]:
def iterate_through_url_list_1(url_list):
    data_list = []
    for count, title_url in enumerate(url_list):
        time.sleep(0.05)
        with open("data_list_1.pkl", "wb") as picklefile:
            pickle.dump(data_list, picklefile)
        movie_data = find_movie_data(title_url)
        if movie_data: 
            data_list.append(movie_data)
        else:
            continue
        if count % 50 == 0:
            time.sleep(1)
            print('Processing Next 50')
    return data_list

In [47]:
def iterate_through_url_list_2(url_list):
    data_list = []
    for count, title_url in enumerate(url_list):
        time.sleep(0.05)
        with open("data_list_2.pkl", "wb") as picklefile:
            pickle.dump(data_list, picklefile)
        movie_data = find_movie_data(title_url)
        if movie_data: 
            data_list.append(movie_data)
        else:
            continue
        if count % 50 == 0:
            time.sleep(1)
            print('Processing Next 50')
    return data_list

In [48]:
def iterate_through_url_list_3(url_list):
    data_list = []
    for count, title_url in enumerate(url_list):
        time.sleep(0.05)
        with open("data_list_3.pkl", "wb") as picklefile:
            pickle.dump(data_list, picklefile)
        movie_data = find_movie_data(title_url)
        if movie_data: 
            data_list.append(movie_data)
        else:
            continue
        if count % 50 == 0:
            time.sleep(1)
            print('Processing Next 50')
    return data_list

In [49]:
def iterate_through_url_list_4(url_list):
    data_list = []
    for count, title_url in enumerate(url_list):
        time.sleep(0.05)
        with open("data_list_4.pkl", "wb") as picklefile:
            pickle.dump(data_list, picklefile)
        movie_data = find_movie_data(title_url)
        if movie_data: 
            data_list.append(movie_data)
        else:
            continue
        if count % 50 == 0:
            time.sleep(1)
            print('Processing Next 50')
    return data_list

In [50]:
def iterate_through_url_list_5(url_list):
    data_list = []
    for count, title_url in enumerate(url_list):
        time.sleep(0.05)
        with open("data_list_5.pkl", "wb") as picklefile:
            pickle.dump(data_list, picklefile)
        movie_data = find_movie_data(title_url)
        if movie_data: 
            data_list.append(movie_data)
        else:
            continue
        if count % 50 == 0:
            time.sleep(1)
            print('Processing Next 50')
    return data_list

In [51]:
iterate_through_url_list_1(list_of_urls_1)

SCRAPING Justice Is Mind
SCRAPING Justice Is Mind
SCRAPING Justice Is Mind
Processing Next 50
SCRAPING Red Cherry
SCRAPING Red Cherry
SCRAPING Red Cherry
SCRAPING Today's Special
SCRAPING Today's Special
SCRAPING Today's Special
SCRAPING Glastonbury
SCRAPING Glastonbury
SCRAPING Glastonbury
SCRAPING Love Me True
SCRAPING Love Me True
SCRAPING Love Me True
SCRAPING The Maltese Falcon
SCRAPING The Maltese Falcon
SCRAPING The Maltese Falcon
SCRAPING How Much Does Your Building Weigh, Mr. Foster?
SCRAPING How Much Does Your Building Weigh, Mr. Foster?
SCRAPING How Much Does Your Building Weigh, Mr. Foster?
SCRAPING Hearts and Minds
SCRAPING Hearts and Minds
SCRAPING Hearts and Minds
SCRAPING Leaving Las Vegas
SCRAPING Leaving Las Vegas
SCRAPING Leaving Las Vegas
SCRAPING The We and the I
SCRAPING The We and the I
SCRAPING The We and the I
SCRAPING The Wrestler
SCRAPING The Wrestler
SCRAPING The Wrestler
SCRAPING Yes
SCRAPING Yes
SCRAPING Yes
SCRAPING Remember
SCRAPING Remember
SCRAPING Rem

[('Justice Is Mind',
  'The Ashton Times',
  'Unrated',
  'Drama',
  nan,
  datetime.datetime(2013, 8, 18, 0, 0),
  14024,
  0,
  5800,
  1,
  1,
  0),
 ("Today's Special",
  'Vitagraph',
  'R',
  'Comedy',
  nan,
  datetime.datetime(2010, 11, 19, 0, 0),
  317831,
  0,
  95400,
  32,
  55,
  datetime.datetime(2010, 12, 16, 0, 0)),
 ('Glastonbury',
  'ThinkFilm',
  'R',
  'Documentary',
  nan,
  datetime.datetime(2007, 2, 23, 0, 0),
  8419,
  193622,
  1400,
  95,
  3,
  datetime.datetime(2007, 4, 12, 0, 0)),
 ('Love Me True',
  'Indican',
  'Unrated',
  'Comedy / Drama',
  nan,
  datetime.datetime(2016, 8, 12, 0, 0),
  10061,
  0,
  5600,
  74,
  2,
  0),
 ('How Much Does Your Building Weigh, Mr. Foster?',
  'First Run',
  'Unrated',
  'Documentary',
  nan,
  datetime.datetime(2012, 1, 25, 0, 0),
  13013,
  0,
  2900,
  80,
  4,
  0),
 ('Hearts and Minds',
  'Rialto',
  'R',
  'Unknown',
  nan,
  datetime.datetime(2004, 10, 22, 0, 0),
  28754,
  0,
  11600,
  87,
  2,
  datetime.dateti

In [52]:
iterate_through_url_list_2(list_of_urls_2)

SCRAPING Five Minutes of Heaven
SCRAPING Five Minutes of Heaven
SCRAPING Five Minutes of Heaven
Processing Next 50
SCRAPING Blood Alley
SCRAPING Blood Alley
SCRAPING Blood Alley
SCRAPING Expelled: No Intelligence Allowed
SCRAPING Expelled: No Intelligence Allowed
SCRAPING Expelled: No Intelligence Allowed
SCRAPING Teen Witch
SCRAPING Teen Witch
SCRAPING Teen Witch
SCRAPING The Way He Looks
SCRAPING The Way He Looks
SCRAPING The Way He Looks
SCRAPING Boiler Room
SCRAPING Boiler Room
SCRAPING Boiler Room
SCRAPING Marvin the Martian  - Box Office Mojo
SCRAPING Marvin the Martian  - Box Office Mojo
SCRAPING Marvin the Martian  - Box Office Mojo
SCRAPING Battle in Heaven
SCRAPING Battle in Heaven
SCRAPING Battle in Heaven
SCRAPING Bailey's Billions
SCRAPING Bailey's Billions
SCRAPING Bailey's Billions
SCRAPING The Edge of Seventeen
SCRAPING The Edge of Seventeen
SCRAPING The Edge of Seventeen
SCRAPING Grand Hotel
SCRAPING Grand Hotel
SCRAPING Grand Hotel
SCRAPING Osama
SCRAPING Osama
SCRAPI

[('Five Minutes of Heaven',
  'IFC',
  'R',
  'Crime Drama',
  nan,
  datetime.datetime(2009, 8, 21, 0, 0),
  15676,
  72230,
  6100,
  79,
  2,
  datetime.datetime(2009, 9, 3, 0, 0)),
 ('Expelled: No Intelligence Allowed',
  'Rocky Mountain Pictures',
  'PG',
  'Documentary',
  nan,
  datetime.datetime(2008, 4, 18, 0, 0),
  7720487,
  0,
  3488100,
  10,
  1052,
  datetime.datetime(2008, 10, 19, 0, 0)),
 ('The Way He Looks',
  'Strand',
  'Unrated',
  'Foreign',
  nan,
  datetime.datetime(2014, 11, 7, 0, 0),
  101451,
  1058000,
  26700,
  51,
  14,
  datetime.datetime(2015, 3, 5, 0, 0)),
 ('Boiler Room',
  'New Line',
  'R',
  'Drama',
  '7',
  datetime.datetime(2000, 2, 18, 0, 0),
  16970581,
  11809674,
  8980700,
  1335,
  1335,
  0),
 ('Battle in Heaven',
  'Tartan',
  'Unrated',
  'Foreign',
  nan,
  datetime.datetime(2006, 2, 17, 0, 0),
  70899,
  182628,
  26200,
  64,
  5,
  datetime.datetime(2006, 6, 25, 0, 0)),
 ("Bailey's Billions",
  'Echo Bridge Entertainment',
  'G',
  

In [53]:
iterate_through_url_list_3(list_of_urls_3)

SCRAPING Harley Davidson and the Marlboro Man
SCRAPING Harley Davidson and the Marlboro Man
SCRAPING Harley Davidson and the Marlboro Man
SCRAPING An American Affair
SCRAPING An American Affair
SCRAPING An American Affair
SCRAPING The Pillow Book
SCRAPING The Pillow Book
SCRAPING The Pillow Book
SCRAPING Vice Versa
SCRAPING Vice Versa
SCRAPING Vice Versa
SCRAPING M
SCRAPING M
SCRAPING M
SCRAPING The Conjuring
SCRAPING The Conjuring
SCRAPING The Conjuring
SCRAPING His Girl Friday
SCRAPING His Girl Friday
SCRAPING His Girl Friday
SCRAPING Tommy
SCRAPING Tommy
SCRAPING Tommy
SCRAPING Volunteers
SCRAPING Volunteers
SCRAPING Volunteers
SCRAPING Brutal Beauty: Tales of the Rose City Rollers
SCRAPING Brutal Beauty: Tales of the Rose City Rollers
SCRAPING Brutal Beauty: Tales of the Rose City Rollers
SCRAPING Yaavarum Nalam
SCRAPING Yaavarum Nalam
SCRAPING Yaavarum Nalam
SCRAPING Altiplano
SCRAPING Altiplano
SCRAPING Altiplano
SCRAPING Koi... Mil Gaya
SCRAPING Koi... Mil Gaya
SCRAPING Koi... M

[('An American Affair',
  'Screen Media',
  'R',
  'Drama',
  nan,
  datetime.datetime(2009, 2, 27, 0, 0),
  28044,
  0,
  13200,
  70,
  2,
  datetime.datetime(2009, 3, 26, 0, 0)),
 ('The Conjuring',
  'Warner Bros. (New Line)',
  'R',
  'Horror',
  '20',
  datetime.datetime(2013, 7, 19, 0, 0),
  137400141,
  180600000,
  45005200,
  1,
  3115,
  datetime.datetime(2013, 10, 31, 0, 0)),
 ('Brutal Beauty: Tales of the Rose City Rollers',
  'Cinema Purgatorio',
  'Unrated',
  'Documentary',
  nan,
  datetime.datetime(2010, 1, 8, 0, 0),
  9677,
  0,
  0,
  196,
  196,
  0),
 ('Yaavarum Nalam',
  'AdLabs',
  'Unrated',
  'Foreign',
  nan,
  datetime.datetime(2009, 3, 6, 0, 0),
  49043,
  0,
  12500,
  68,
  6,
  datetime.datetime(2009, 4, 2, 0, 0)),
 ('Altiplano',
  'First Run',
  'Unrated',
  'Drama',
  nan,
  datetime.datetime(2010, 8, 20, 0, 0),
  2961,
  0,
  1400,
  92,
  1,
  datetime.datetime(2010, 10, 7, 0, 0)),
 ('Koi... Mil Gaya',
  'Yash Raj',
  'Unrated',
  'Unknown',
  nan,
  

In [54]:
iterate_through_url_list_4(list_of_urls_4)

SCRAPING The Secret of Kells
SCRAPING The Secret of Kells
SCRAPING The Secret of Kells
Processing Next 50
SCRAPING It Always Rains on Sunday
SCRAPING It Always Rains on Sunday
SCRAPING It Always Rains on Sunday
SCRAPING The Haunting in Connecticut
SCRAPING The Haunting in Connecticut
SCRAPING The Haunting in Connecticut
SCRAPING Everybody Wants to Be Italian
SCRAPING Everybody Wants to Be Italian
SCRAPING Everybody Wants to Be Italian
SCRAPING Magdalena, The Unholy Saint
SCRAPING Magdalena, The Unholy Saint
SCRAPING Magdalena, The Unholy Saint
SCRAPING Red Lights
SCRAPING Red Lights
SCRAPING Red Lights
SCRAPING The Dawn Patrol
SCRAPING The Dawn Patrol
SCRAPING The Dawn Patrol
SCRAPING Nola
SCRAPING Nola
SCRAPING Nola
SCRAPING Munger Road
SCRAPING Munger Road
SCRAPING Munger Road
SCRAPING Open Grave
SCRAPING Open Grave
SCRAPING Open Grave
SCRAPING Photographic Memory
SCRAPING Photographic Memory
SCRAPING Photographic Memory
SCRAPING Closet Monster
SCRAPING Closet Monster
SCRAPING Closet

[('The Secret of Kells',
  'GKIDS',
  'Unrated',
  'Animation',
  '8',
  datetime.datetime(2010, 3, 5, 0, 0),
  676775,
  62679,
  42200,
  45,
  37,
  datetime.datetime(2010, 7, 29, 0, 0)),
 ('It Always Rains on Sunday',
  'Rialto',
  'Unrated',
  'Crime',
  nan,
  datetime.datetime(2008, 3, 7, 0, 0),
  14276,
  0,
  8400,
  83,
  1,
  datetime.datetime(2008, 3, 13, 0, 0)),
 ('The Haunting in Connecticut',
  'Lionsgate',
  'PG-13',
  'Horror',
  nan,
  datetime.datetime(2009, 3, 27, 0, 0),
  55389516,
  22138216,
  25996000,
  2,
  2732,
  datetime.datetime(2009, 5, 14, 0, 0)),
 ('Everybody Wants to Be Italian',
  'Roadside Attractions',
  'R',
  'Romantic Comedy',
  '3',
  datetime.datetime(2008, 9, 5, 0, 0),
  351416,
  181310,
  232300,
  33,
  98,
  datetime.datetime(2008, 10, 16, 0, 0)),
 ('Magdalena, The Unholy Saint',
  'Unico Entertainment',
  'Unrated',
  'Foreign',
  nan,
  datetime.datetime(2005, 3, 11, 0, 0),
  6470,
  0,
  8500,
  88,
  3,
  datetime.datetime(2005, 3, 13,

In [55]:
iterate_through_url_list_5(list_of_urls_5)

SCRAPING Bill Cunningham New York
SCRAPING Bill Cunningham New York
SCRAPING Bill Cunningham New York
Processing Next 50
SCRAPING The Right Stuff
SCRAPING The Right Stuff
SCRAPING The Right Stuff
SCRAPING Ned Kelly
SCRAPING Ned Kelly
SCRAPING Ned Kelly
SCRAPING Race You to the Bottom
SCRAPING Race You to the Bottom
SCRAPING Race You to the Bottom
SCRAPING Hoodwinked
SCRAPING Hoodwinked
SCRAPING Hoodwinked
SCRAPING Dr. Jekyll and Mr. Hyde
SCRAPING Dr. Jekyll and Mr. Hyde
SCRAPING Dr. Jekyll and Mr. Hyde
SCRAPING Adam's Apples
SCRAPING Adam's Apples
SCRAPING Adam's Apples
SCRAPING Beyond Therapy
SCRAPING Beyond Therapy
SCRAPING Beyond Therapy
SCRAPING The Watcher
SCRAPING The Watcher
SCRAPING The Watcher
SCRAPING The Cat in the Hat
SCRAPING The Cat in the Hat
SCRAPING The Cat in the Hat
SCRAPING Chariots of Fire
SCRAPING Chariots of Fire
SCRAPING Chariots of Fire
SCRAPING Generation Iron
SCRAPING Generation Iron
SCRAPING Generation Iron
SCRAPING Nobody's Perfekt
SCRAPING Nobody's Perfekt

[('Bill Cunningham New York',
  'Zeitgeist',
  'Unrated',
  'Documentary',
  nan,
  datetime.datetime(2011, 3, 16, 0, 0),
  1510026,
  0,
  36100,
  53,
  34,
  datetime.datetime(2011, 12, 1, 0, 0)),
 ('Ned Kelly',
  'Focus Features',
  'R',
  'Unknown',
  nan,
  datetime.datetime(2004, 3, 26, 0, 0),
  86959,
  6498557,
  59300,
  58,
  22,
  0),
 ('Race You to the Bottom',
  'Regent Releasing',
  'R',
  'Romance',
  nan,
  datetime.datetime(2007, 3, 30, 0, 0),
  5468,
  0,
  1900,
  100,
  1,
  datetime.datetime(2007, 6, 28, 0, 0)),
 ('Hoodwinked',
  'Weinstein Company',
  'PG',
  'Animation',
  nan,
  datetime.datetime(2005, 12, 16, 0, 0),
  51386611,
  58626556,
  15961500,
  3,
  3020,
  datetime.datetime(2006, 5, 11, 0, 0)),
 ("Adam's Apples",
  'Outsider Pictures',
  'R',
  'Foreign',
  nan,
  datetime.datetime(2007, 3, 16, 0, 0),
  1305,
  2420272,
  1600,
  108,
  1,
  datetime.datetime(2007, 3, 18, 0, 0)),
 ('The Watcher',
  'Universal',
  'R',
  'Thriller',
  '30',
  datetime

In [56]:
with open("data_list_1.pkl", 'rb') as picklefile: 
    movie_ids = pickle.load(picklefile)
    
print('Number of movies w/ data: ', len(movie_ids))
print('Number of movies checked: ', len(list_of_urls))

Number of movies w/ data:  2594
Number of movies checked:  16680


In [57]:
with open("data_list_1.pkl", 'rb') as picklefile: 
    movie_data = pickle.load(picklefile)

In [58]:
df = pd.DataFrame(movie_data)
df

0   \
0                                    Justice Is Mind   
1                                    Today's Special   
2                                        Glastonbury   
3                                       Love Me True   
4     How Much Does Your Building Weigh, Mr. Foster?   
5                                   Hearts and Minds   
6                                   The We and the I   
7                                       The Wrestler   
8                                                Yes   
9                                           Remember   
10                                       Bright Star   
11                               All About My Mother   
12                    Book of Shadows: Blair Witch 2   
13                                   Caesar Must Die   
14                                           Elysium   
15                         Instructions Not Included   
16                                 A Perfect Getaway   
17                                      Pearl Button   
18                                        Convention   
19                                   Lost in Beijing   
20                               Soldiers of Fortune   
21                         After Dark's Horrorfest 2   
22                                     The Nut Job 2   
23                         The Powerpuff Girls Movie   
24                                   Straight-Jacket   
25                                              Pawn   
26                   The Perks of Being a Wallflower   
27         Middle School: The Worst Years of My Life   
28                                   The Fallen Idol   
29                                       Going Under   
...                                              ...   
2564                                  To Save a Life   
2565                                Charlie's Angels   
2566                        Beyond the Farthest Star   
2567                               Keys to the House   
2568                                      Panic Room   
2569                                   Play the Game   
2570                                   R... Rajkumar   
2571                                   Herman U.S.A.   
2572                                         9 Songs   
2573                                    The American   
2574                                       Hat Trick   
2575                             Midnight Meat Train   
2576                 How to Make Money Selling Drugs   
2577                 Garfield: A Tail of Two Kitties   
2578                      The Prince of Central Park   
2579                            Charlie Wilson's War   
2580             Youssou N'Dour: I Bring What I Love   
2581                        Where God Left His Shoes   
2582                                     The D Train   
2583                              A Map of the World   
2584                                        Gomorrah   
2585                          The Princess of France   
2586                                 Furry Vengeance   
2587                                     Deuces Wild   
2588                         They're Out of Business   
2589                      When Comedy Went to School   
2590                                Four Christmases   
2591                                        Freetown   
2592          The Autobiography of Nicolae Ceausescu   
2593                                         Korhram   

                              1              2                   3        4   \
0               The Ashton Times        Unrated               Drama      NaN   
1                      Vitagraph              R              Comedy      NaN   
2                      ThinkFilm              R         Documentary      NaN   
3                        Indican        Unrated      Comedy / Drama      NaN   
4                      First Run        Unrated         Documentary      NaN   
5                         Rialto              R             Unknown      NaN   
6              Pa

## Scrape weekly data

In [126]:
# all weekly URLs

weekly_prefix = 'http://www.boxofficemojo.com/weekly/?yr='
weekly_suffix = '&p=.htm'
year_index = [i for i in range(1999,2017)]
weekly_index = []
for i in year_index:
    weekly_index.append(weekly_prefix + str(i) + weekly_suffix)

weekly_index

['http://www.boxofficemojo.com/weekly/?yr=1999&p=.htm',
 'http://www.boxofficemojo.com/weekly/?yr=2000&p=.htm',
 'http://www.boxofficemojo.com/weekly/?yr=2001&p=.htm',
 'http://www.boxofficemojo.com/weekly/?yr=2002&p=.htm',
 'http://www.boxofficemojo.com/weekly/?yr=2003&p=.htm',
 'http://www.boxofficemojo.com/weekly/?yr=2004&p=.htm',
 'http://www.boxofficemojo.com/weekly/?yr=2005&p=.htm',
 'http://www.boxofficemojo.com/weekly/?yr=2006&p=.htm',
 'http://www.boxofficemojo.com/weekly/?yr=2007&p=.htm',
 'http://www.boxofficemojo.com/weekly/?yr=2008&p=.htm',
 'http://www.boxofficemojo.com/weekly/?yr=2009&p=.htm',
 'http://www.boxofficemojo.com/weekly/?yr=2010&p=.htm',
 'http://www.boxofficemojo.com/weekly/?yr=2011&p=.htm',
 'http://www.boxofficemojo.com/weekly/?yr=2012&p=.htm',
 'http://www.boxofficemojo.com/weekly/?yr=2013&p=.htm',
 'http://www.boxofficemojo.com/weekly/?yr=2014&p=.htm',
 'http://www.boxofficemojo.com/weekly/?yr=2015&p=.htm',
 'http://www.boxofficemojo.com/weekly/?yr=2016&p

In [127]:
def find_weekly_data(url):
    try:
        page = requests.get(url).text
    except:
        return None
    else:
        soup = BeautifulSoup(page,'lxml')
        a = soup.find_all('table')[3].find_all('td')
        
        # get movie title
        week_of_year = []
        counter = 15
        for i, r in enumerate(a):
            if i == counter:
                week_of_year.append(r.text)
                counter +=8
            
        week_movies_out = []
        counter = 13
        for i, r in enumerate(a):
            if i == counter:
                week_movies_out.append(r.text)
                counter +=8
        
        week_overall_gross = []
        counter = 11
        for i, r in enumerate(a):
            if i == counter:
                week_overall_gross.append(money_to_int(r.text))
                counter +=8
        
        year_list = []
        num = int((len(a)/8) - 1)
        for i in range(num):
            year_list.append(re.findall('\d+', url)[0])
            
    list_of_dfs = pd.DataFrame(dict\
(week_of_year = week_of_year, week_movies_out = week_movies_out, week_overall_gross =  \
week_overall_gross, year_list = year_list))
    
    return list_of_dfs

In [128]:
def iterate_through_weekly_index(url_list):
    data_list = []
    for count, title_url in enumerate(url_list):
        time.sleep(0.05)
        weekly_data = find_weekly_data(title_url)
        if movie_data: 
            data_list.append(weekly_data)
        else:
            continue
        if count % 50 == 0:
            time.sleep(1)
            print('Processing Next 50')
    return data_list

In [129]:
raw_df = iterate_through_weekly_index(weekly_index)

Processing Next 50


In [130]:
variable_list = ['year_'+str(i) for i in range(1999,2017)]
print(variable_list)

['year_1999', 'year_2000', 'year_2001', 'year_2002', 'year_2003', 'year_2004', 'year_2005', 'year_2006', 'year_2007', 'year_2008', 'year_2009', 'year_2010', 'year_2011', 'year_2012', 'year_2013', 'year_2014', 'year_2015', 'year_2016']


In [131]:
year_1999 = raw_df[0]
year_2000 = raw_df[1]
year_2001 = raw_df[2]
year_2002 = raw_df[3]
year_2003 = raw_df[4]
year_2004 = raw_df[5]
year_2005 = raw_df[6]
year_2006 = raw_df[7]
year_2007 = raw_df[8]
year_2008 = raw_df[9]
year_2009 = raw_df[10]
year_2010 = raw_df[11]
year_2011 = raw_df[12]
year_2012 = raw_df[13]
year_2013 = raw_df[14]
year_2014 = raw_df[15]
year_2015 = raw_df[16]
year_2016 = raw_df[17]

df_week = pd.concat([year_1999, year_2000, year_2001, year_2002, 
           year_2003, year_2004, year_2005, year_2006, 
           year_2007, year_2008, year_2009, year_2010, 
           year_2011, year_2012, year_2013, year_2014, 
           year_2015, year_2016], axis=0)
len(df_week)

926

In [132]:
with open("df_week.pkl", "wb") as picklefile:
            pickle.dump(df_week, picklefile)

## Scrape video sales data

In [76]:
# get a list of url for individual movie pages

numbers_url = 'http://www.the-numbers.com/movie/budgets/all'
base_url = 'http://www.the-numbers.com'

In [77]:
page = requests.get(numbers_url).text
soup = BeautifulSoup(page, 'lxml')
soup.prettify

list_of_urls_numbers = []
links = soup.find('table').find_all('a')
for link in links:
    if link.get('href')[:6] == '/movie':
        full_link = base_url + link.get('href')
        list_of_urls_numbers.append(full_link)
        
list_of_urls_numbers

with open('list_of_urls_numbers.pkl', 'wb') as picklefile:
            pickle.dump(list_of_urls_numbers, picklefile)

### Pickle station - list of urls for the-numbers

In [79]:
with open('list_of_urls_numbers.pkl', 'rb') as picklefile: 
    list_of_urls_num = pickle.load(picklefile)
    
print('Number of links: ', len(list_of_urls_num))

Number of links:  5230


In [80]:
def find_numbers_data(urlname):
    try:
        page = requests.get(urlname).text
    except:
        return None
    else:
        soup_num = BeautifulSoup(page,'lxml')
    
        # get movie title
        for title in soup_num:
            try:
                title_str = soup_num.h1.get_text(strip=True)
                title = title_str.split(' (')[0]
                print('SCRAPING ' + title)
            except:
                print('WARNING: unable to get movie title')
                return None
        
        # get Total Domestic Video Sales
        domestic_video_sales = 0
        for domestic_video_sales in soup_num:
            try:
                obj = soup_num.find(text=re.compile('Total Domestic Video Sales'))
                next_value = obj.find_next('td').get_text(strip=True)
                domestic_video_sales = int(next_value.replace('$','').replace(',',''))
            except:
                print('WARNING: no total domestic video sales data returned')
                return None
                
    # return a tuple for each movie with relevant data
    return (title, domestic_video_sales)

In [81]:
def iterate_through_url_list_num(url_list):
    data_list = []
    for count, title_url in enumerate(url_list):
        time.sleep(0.05)
        with open("data_list_num.pkl", "wb") as picklefile:
            pickle.dump(data_list, picklefile)
        num_movie_data = find_numbers_data(title_url)
        if num_movie_data: 
            data_list.append(num_movie_data)
        else:
            continue
        if count % 50 == 0:
            time.sleep(1)
            print('Processing Next 50')
    return data_list

In [82]:
iterate_through_url_list_num(list_of_urls_num)

SCRAPING Avatar
SCRAPING Avatar
SCRAPING Avatar
Processing Next 50
SCRAPING Star Wars Ep. VII: The Force Awakens
SCRAPING Star Wars Ep. VII: The Force Awakens
SCRAPING Star Wars Ep. VII: The Force Awakens
SCRAPING Pirates of the Caribbean: At World's End
SCRAPING Pirates of the Caribbean: At World's End
SCRAPING Pirates of the Caribbean: At World's End
SCRAPING Spectre
SCRAPING Spectre
SCRAPING Spectre
SCRAPING The Dark Knight Rises
SCRAPING The Dark Knight Rises
SCRAPING The Dark Knight Rises
SCRAPING The Lone Ranger
SCRAPING The Lone Ranger
SCRAPING The Lone Ranger
SCRAPING John Carter
SCRAPING John Carter
SCRAPING John Carter
SCRAPING Tangled
SCRAPING Tangled
SCRAPING Tangled
SCRAPING Spider-Man 3
SCRAPING Spider-Man 3
SCRAPING Spider-Man 3
SCRAPING Avengers: Age of Ultron
SCRAPING Avengers: Age of Ultron
SCRAPING Avengers: Age of Ultron
SCRAPING Captain America: Civil War
SCRAPING Captain America: Civil War
SCRAPING Captain America: Civil War
SCRAPING Batman v Superman: Dawn of Jus

[('Avatar', 393900380),
 ('Star Wars Ep. VII: The Force Awakens', 155971910),
 ("Pirates of the Caribbean: At World's End", 318390503),
 ('Spectre', 35290698),
 ('The Dark Knight Rises', 151859615),
 ('The Lone Ranger', 46262814),
 ('John Carter', 37999052),
 ('Tangled', 222454940),
 ('Spider-Man 3', 125738775),
 ('Avengers: Age of Ultron', 76854785),
 ('Batman v Superman: Dawn of Justice', 31109645),
 ('The Hobbit: An Unexpected Journey', 122020546),
 ('Harry Potter and the Half-Blood Prince', 187605374),
 ('The Hobbit: The Desolation of Smaug', 104419434),
 ('The Hobbit: The Battle of the Five Armies', 74473843),
 ('Pirates of the Caribbean: On Stranger Tides', 90117625),
 ('Superman Returns', 85679820),
 ('Quantum of Solace', 60969651),
 ('The Avengers', 232844247),
 ("Pirates of the Caribbean: Dead Man's Chest", 323464171),
 ('Man of Steel', 109226383),
 ('The Chronicles of Narnia: Prince Caspian', 100855949),
 ('The Amazing Spider-Man', 110372707),
 ('Jurassic World', 127398916),


In [85]:
with open("data_list_num.pkl", 'rb') as picklefile: 
    num_data = pickle.load(picklefile)
    
print('Number of movies w/ data: ', len(num_data))
print('Number of movies checked: ', len(list_of_urls_num))

Number of movies w/ data:  1728
Number of movies checked:  5230


In [86]:
df_num = pd.DataFrame(num_data)
df_num

0          1
0                                          Avatar  393900380
1            Star Wars Ep. VII: The Force Awakens  155971910
2        Pirates of the Caribbean: At World's End  318390503
3                                         Spectre   35290698
4                           The Dark Knight Rises  151859615
5                                 The Lone Ranger   46262814
6                                     John Carter   37999052
7                                         Tangled  222454940
8                                    Spider-Man 3  125738775
9                         Avengers: Age of Ultron   76854785
10             Batman v Superman: Dawn of Justice   31109645
11              The Hobbit: An Unexpected Journey  122020546
12         Harry Potter and the Half-Blood Prince  187605374
13            The Hobbit: The Desolation of Smaug  104419434
14      The Hobbit: The Battle of the Five Armies   74473843
15    Pirates of the Caribbean: On Stranger Tides   90117625
16                               Superman Returns   85679820
17                              Quantum of Solace   60969651
18                                   The Avengers  232844247
19     Pirates of the Caribbean: Dead Man's Chest  323464171
20                                   Man of Steel  109226383
21       The Chronicles of Narnia: Prince Caspian  100855949
22                         The Amazing Spider-Man  110372707
23                                 Jurassic World  127398916
24                                 Men in Black 3   57517616
25            Transformers: Revenge of the Fallen  272089802
26                Transformers: Age of Extinction   62916558
27                          X-Men: The Last Stand  145935301
28                                     Robin Hood   63865591
29                                     Battleship   32352469
...                                           ...        ...
1698                                    Fireproof   56764440
1699                             Drinking Buddies     319926
1700     Born to Fly: Elizabeth Streb vs. Gravity      22684
1701                                 Subconscious      22177
1702                                     Roadside       4081
1703                          Paranormal Activity   21492396
1704                                        Brick    5037537
1705                                    Blue Ruin     431348
1706                           Viskningar och rop     140166
1707                                    Rotor DR1      25042
1708                                    Locker 13      11218
1709                            The Looking Glass      15558
1710                              Teeth and Blood       8652
1711                                  The Canyons      18765
1712                              Give Me Shelter       4561
1713                              The Love Letter      67280
1714                            Middle of Nowhere      97274
1715                 Sanctuary; Quite a Conundrum       9419
1716                               Perfect Cowboy       7554
1717                            Une Femme MariÃ©e       8706
1718                                  The Gallows    1200628
1719                            Facing the Giants   41207675
1720                                Cheap Thrills     188098
1721                                 Tiger Orange      54330
1722                                   Queen Crab      46016
1723                  The Brain That Wouldn't Die      16800
1724                               Run, Hide, Die      14664
1725                                     Backmask      74479
1726                      Signed Sealed Delivered     777096
1727                         A Plague So Pleasant      20135

[1728 rows x 2 columns]

## Scrape table from the-numbers

In [89]:
budget_url = 'http://www.the-numbers.com/movie/budgets/all'

In [90]:
response = requests.get(budget_url)
page = response.text
soup = BeautifulSoup(page,'lxml')

In [97]:
movie_htm = soup.find('table').find_all('a')
movie_tab = soup.find('table').find_all('td')

In [117]:
movie_list = []
counter = 1
for i, r in enumerate(movie_htm):
    if i == counter:
        movie_list.append(r.text)
        counter +=2
print(len(movie_list))

5230


In [118]:
bud_list = []
counter = 3
for i, r in enumerate(movie_tab):
    if i == counter:
        bud_list.append(money_to_int(r.text))
        counter += 6
# print(len(bud_list))

In [119]:
dg_list = []
counter = 4
for i, r in enumerate(movie_tab):
    if i == counter:
        dg_list.append(money_to_int(r.text))
        counter += 6
print(len(dg_list))

5230


In [120]:
wwg_list = []
counter = 5
for i, r in enumerate(movie_tab):
    if i == counter:
        wwg_list.append(money_to_int(r.text))
        counter += 6
print(len(wwg_list))

5230


In [121]:
numbers_df = pd.DataFrame(dict\
(movie_title = movie_list, prod_budget= bud_list, dom_gross =  \
dg_list, world_gross= wwg_list))

In [122]:
numbers_df.head(10)

dom_gross                               movie_title  prod_budget  \
0  760507625                                    Avatar    425000000   
1  936662225      Star Wars Ep. VII: The Force Awakens    306000000   
2  309420425  Pirates of the Caribbean: At World's End    300000000   
3  200074175                                   Spectre    300000000   
4  448139099                     The Dark Knight Rises    275000000   
5   89302115                           The Lone Ranger    275000000   
6   73058679                               John Carter    275000000   
7  200821936                                   Tangled    260000000   
8  336530303                              Spider-Man 3    258000000   
9  459005868                   Avengers: Age of Ultron    250000000   

   world_gross  
0   2783918982  
1   2058662225  
2    963420425  
3    879620923  
4   1084439099  
5    260002115  
6    282778100  
7    586581936  
8    890875303  
9   1404705868

In [123]:
numbers_df.dtypes

dom_gross       int64
movie_title    object
prod_budget     int64
world_gross     int64
dtype: object

In [124]:
with open('budget_numbers.pkl', 'wb') as picklefile:
            pickle.dump(numbers_df, picklefile)

In [125]:
with open("budget_numbers.pkl", 'rb') as picklefile: 
    df_numbers = pickle.load(picklefile)
    
print('Number of movies w/ data: ', len(df_numbers))

Number of movies w/ data:  5230
